# CatBoost modeling

### 1. Load Dataset

In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import pandas as pd

train = pd.read_csv('../../data/prepared_train.csv')
test = pd.read_csv('../../data/prepared_test.csv')

### 2. Train, Validation, Test split

In [2]:
from sklearn.model_selection import StratifiedShuffleSplit

group = ['lane_count', 'road_rating', 'weight_restricted', 'maximum_speed_limit']

split = StratifiedShuffleSplit(n_splits=1, test_size=0.2, random_state=42)

for train_index, val_index in split.split(train, train[group]):
    train_set = train.loc[train_index]
    val_set = train.loc[val_index]

### 3. Scaling

In [3]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
cat_features = ['lane_count', 'road_rating', 'base_hour', 'day_of_week', 
                'maximum_speed_limit', 'weight_restricted', 'month', 'day', 'hour']
cat_features += ['target']

train_ = scaler.fit_transform(train_set.loc[:, train_set.columns.drop(cat_features)])
train_ = pd.DataFrame(train_, columns=train_set.columns.drop(cat_features).values)
train_[cat_features] = train_set[cat_features].values
train_set = train_
train_ = 0

val_ = scaler.transform(val_set.loc[:, val_set.columns.drop(cat_features)])
val_ = pd.DataFrame(val_, columns=val_set.columns.drop(cat_features).values)
val_[cat_features] = val_set[cat_features].values
val_set = val_
val_ = 0

cat_features = ['lane_count', 'road_rating', 'base_hour', 'day_of_week', 
                'maximum_speed_limit', 'weight_restricted', 'month', 'day', 'hour']

test_ = scaler.transform(test.loc[:, test.columns.drop(cat_features)])
test_ = pd.DataFrame(test_, columns=test.columns.drop(cat_features).values)
test_[cat_features] = test[cat_features].values
test = test_
test_ = 0

### 4. catboost model

In [4]:
from catboost import CatBoostRegressor
from sklearn.model_selection import train_test_split

params = {
    "iterations" : 100000,
    "early_stopping_rounds" : 100,
    "learning_rate" : 0.01,
    "min_data_in_leaf" : 24,
    "max_depth" : 12,
    "eval_metric" : 'MAE',
    "task_type" : "GPU",
    "devices" : '0',
    "reg_lambda" : 5.0244,
    "leaf_estimation_iterations" : 7,
    "bagging_temperature" : 0.07156,
    "random_state" : 42,
}

model = CatBoostRegressor(**params)

### 5. train

In [5]:
from catboost import Pool
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
sns.set() # setting seaborn default for plots

X_val = val_set.drop(columns='target').values
y_val = val_set['target'].values

X_train = train_set.drop(columns='target').values
y_train = train_set['target'].values

train_pool = Pool(X_train, y_train)
eval_pool = Pool(X_val, y_val)

trained_model = model.fit(train_pool, eval_set=eval_pool, verbose=True)

Default metric period is 5 because MAE is/are not implemented for GPU


0:	learn: 13.1227956	test: 13.1455952	best: 13.1455952 (0)	total: 51.1ms	remaining: 2h 50m 24s
1:	total: 102ms	remaining: 2h 49m 13s
2:	total: 151ms	remaining: 2h 48m
3:	total: 198ms	remaining: 2h 44m 35s
4:	total: 243ms	remaining: 2h 41m 59s
5:	learn: 12.6495330	test: 12.6719639	best: 12.6719639 (5)	total: 289ms	remaining: 2h 40m 46s
6:	total: 335ms	remaining: 2h 39m 29s
7:	total: 381ms	remaining: 2h 38m 39s
8:	total: 427ms	remaining: 2h 38m 2s
9:	total: 473ms	remaining: 2h 37m 36s
10:	learn: 12.1991208	test: 12.2211809	best: 12.2211809 (10)	total: 521ms	remaining: 2h 37m 58s
11:	total: 568ms	remaining: 2h 37m 46s
12:	total: 614ms	remaining: 2h 37m 19s
13:	total: 659ms	remaining: 2h 36m 53s
14:	total: 705ms	remaining: 2h 36m 41s
15:	learn: 11.7793518	test: 11.8008549	best: 11.8008549 (15)	total: 753ms	remaining: 2h 36m 57s
16:	total: 799ms	remaining: 2h 36m 42s
17:	total: 845ms	remaining: 2h 36m 30s
18:	total: 892ms	remaining: 2h 36m 27s
19:	total: 938ms	remaining: 2h 36m 23s
20:	lear

165:	learn: 6.2069890	test: 6.2137642	best: 6.2137642 (165)	total: 7.81s	remaining: 2h 36m 43s
166:	total: 7.86s	remaining: 2h 36m 46s
167:	total: 7.91s	remaining: 2h 36m 47s
168:	total: 7.96s	remaining: 2h 36m 49s
169:	total: 8s	remaining: 2h 36m 48s
170:	learn: 6.1463334	test: 6.1529869	best: 6.1529869 (170)	total: 8.05s	remaining: 2h 36m 51s
171:	total: 8.1s	remaining: 2h 36m 52s
172:	total: 8.15s	remaining: 2h 36m 53s
173:	total: 8.2s	remaining: 2h 36m 55s
174:	total: 8.25s	remaining: 2h 36m 57s
175:	learn: 6.0908515	test: 6.0973380	best: 6.0973380 (175)	total: 8.29s	remaining: 2h 36m 58s
176:	total: 8.34s	remaining: 2h 36m 59s
177:	total: 8.39s	remaining: 2h 37m
178:	total: 8.44s	remaining: 2h 37m
179:	total: 8.49s	remaining: 2h 37m 2s
180:	learn: 6.0369702	test: 6.0433074	best: 6.0433074 (180)	total: 8.54s	remaining: 2h 37m 2s
181:	total: 8.58s	remaining: 2h 37m 1s
182:	total: 8.63s	remaining: 2h 37m 4s
183:	total: 8.68s	remaining: 2h 37m 4s
184:	total: 8.72s	remaining: 2h 37m 4s

330:	learn: 5.1793831	test: 5.1834093	best: 5.1834093 (330)	total: 15.7s	remaining: 2h 37m 59s
331:	total: 15.8s	remaining: 2h 37m 59s
332:	total: 15.8s	remaining: 2h 38m
333:	total: 15.9s	remaining: 2h 38m
334:	total: 15.9s	remaining: 2h 37m 59s
335:	learn: 5.1633628	test: 5.1674704	best: 5.1674704 (335)	total: 16s	remaining: 2h 38m 1s
336:	total: 16s	remaining: 2h 38m 1s
337:	total: 16.1s	remaining: 2h 38m 1s
338:	total: 16.1s	remaining: 2h 38m 1s
339:	total: 16.1s	remaining: 2h 38m 1s
340:	learn: 5.1500806	test: 5.1542701	best: 5.1542701 (340)	total: 16.2s	remaining: 2h 38m 3s
341:	total: 16.2s	remaining: 2h 38m 4s
342:	total: 16.3s	remaining: 2h 38m 3s
343:	total: 16.3s	remaining: 2h 38m 4s
344:	total: 16.4s	remaining: 2h 38m 4s
345:	learn: 5.1358327	test: 5.1400381	best: 5.1400381 (345)	total: 16.4s	remaining: 2h 38m 5s
346:	total: 16.5s	remaining: 2h 38m 5s
347:	total: 16.5s	remaining: 2h 38m 5s
348:	total: 16.6s	remaining: 2h 38m 6s
349:	total: 16.6s	remaining: 2h 38m 7s
350:	le

495:	learn: 4.8534111	test: 4.8581230	best: 4.8581230 (495)	total: 23.6s	remaining: 2h 38m 9s
496:	total: 23.6s	remaining: 2h 38m 9s
497:	total: 23.7s	remaining: 2h 38m 9s
498:	total: 23.7s	remaining: 2h 38m 10s
499:	total: 23.8s	remaining: 2h 38m 10s
500:	learn: 4.8463842	test: 4.8511392	best: 4.8511392 (500)	total: 23.8s	remaining: 2h 38m 10s
501:	total: 23.9s	remaining: 2h 38m 12s
502:	total: 23.9s	remaining: 2h 38m 12s
503:	total: 24s	remaining: 2h 38m 11s
504:	total: 24s	remaining: 2h 38m 10s
505:	learn: 4.8391408	test: 4.8439485	best: 4.8439485 (505)	total: 24.1s	remaining: 2h 38m 10s
506:	total: 24.1s	remaining: 2h 38m 10s
507:	total: 24.2s	remaining: 2h 38m 9s
508:	total: 24.2s	remaining: 2h 38m 11s
509:	total: 24.3s	remaining: 2h 38m 10s
510:	learn: 4.8313700	test: 4.8362244	best: 4.8362244 (510)	total: 24.3s	remaining: 2h 38m 9s
511:	total: 24.4s	remaining: 2h 38m 10s
512:	total: 24.4s	remaining: 2h 38m 11s
513:	total: 24.5s	remaining: 2h 38m 12s
514:	total: 24.5s	remaining: 

...

62502:	total: 52m 29s	remaining: 1h 55m 27s
62503:	total: 52m 29s	remaining: 1h 55m 27s
62504:	total: 52m 29s	remaining: 1h 55m 27s
62505:	learn: 2.4777141	test: 2.9280091	best: 2.9280088 (62504)	total: 52m 29s	remaining: 1h 55m 27s
62506:	total: 52m 29s	remaining: 1h 55m 27s
62507:	total: 52m 29s	remaining: 1h 55m 27s
62508:	total: 52m 29s	remaining: 1h 55m 27s
62509:	total: 52m 29s	remaining: 1h 55m 27s
62510:	learn: 2.4776636	test: 2.9280062	best: 2.9280049 (62509)	total: 52m 29s	remaining: 1h 55m 26s
62511:	total: 52m 29s	remaining: 1h 55m 26s
62512:	total: 52m 29s	remaining: 1h 55m 26s
62513:	total: 52m 29s	remaining: 1h 55m 26s
62514:	total: 52m 29s	remaining: 1h 55m 26s
62515:	learn: 2.4776312	test: 2.9279977	best: 2.9279977 (62515)	total: 52m 29s	remaining: 1h 55m 26s
62516:	total: 52m 29s	remaining: 1h 55m 26s
62517:	total: 52m 29s	remaining: 1h 55m 26s
62518:	total: 52m 29s	remaining: 1h 55m 26s
62519:	total: 52m 29s	remaining: 1h 55m 26s
62520:	learn: 2.4775932	test: 2.92798

62653:	total: 52m 36s	remaining: 1h 55m 19s
62654:	total: 52m 36s	remaining: 1h 55m 19s
62655:	learn: 2.4766679	test: 2.9278677	best: 2.9278669 (62654)	total: 52m 36s	remaining: 1h 55m 19s
62656:	total: 52m 36s	remaining: 1h 55m 19s
62657:	total: 52m 36s	remaining: 1h 55m 19s
62658:	total: 52m 36s	remaining: 1h 55m 19s
62659:	total: 52m 37s	remaining: 1h 55m 19s
62660:	learn: 2.4766312	test: 2.9278581	best: 2.9278581 (62660)	total: 52m 37s	remaining: 1h 55m 19s
62661:	total: 52m 37s	remaining: 1h 55m 19s
62662:	total: 52m 37s	remaining: 1h 55m 19s
62663:	total: 52m 37s	remaining: 1h 55m 19s
62664:	total: 52m 37s	remaining: 1h 55m 19s
62665:	learn: 2.4766043	test: 2.9278528	best: 2.9278528 (62665)	total: 52m 37s	remaining: 1h 55m 19s
62666:	total: 52m 37s	remaining: 1h 55m 19s
62667:	total: 52m 37s	remaining: 1h 55m 19s
62668:	total: 52m 37s	remaining: 1h 55m 19s
62669:	total: 52m 37s	remaining: 1h 55m 19s
62670:	learn: 2.4765620	test: 2.9278453	best: 2.9278445 (62669)	total: 52m 37s	re

62804:	total: 52m 44s	remaining: 1h 55m 12s
62805:	learn: 2.4756043	test: 2.9277243	best: 2.9277243 (62805)	total: 52m 44s	remaining: 1h 55m 12s
62806:	total: 52m 44s	remaining: 1h 55m 12s
62807:	total: 52m 44s	remaining: 1h 55m 12s
62808:	total: 52m 44s	remaining: 1h 55m 12s
62809:	total: 52m 44s	remaining: 1h 55m 12s
62810:	learn: 2.4755721	test: 2.9277161	best: 2.9277161 (62810)	total: 52m 44s	remaining: 1h 55m 12s
62811:	total: 52m 44s	remaining: 1h 55m 12s
62812:	total: 52m 44s	remaining: 1h 55m 12s
62813:	total: 52m 44s	remaining: 1h 55m 12s
62814:	total: 52m 44s	remaining: 1h 55m 12s
62815:	learn: 2.4755349	test: 2.9277142	best: 2.9277121 (62814)	total: 52m 44s	remaining: 1h 55m 11s
62816:	total: 52m 45s	remaining: 1h 55m 11s
62817:	total: 52m 45s	remaining: 1h 55m 11s
62818:	total: 52m 45s	remaining: 1h 55m 11s
62819:	total: 52m 45s	remaining: 1h 55m 11s
62820:	learn: 2.4755067	test: 2.9277087	best: 2.9277071 (62819)	total: 52m 45s	remaining: 1h 55m 11s
62821:	total: 52m 45s	re

62957:	total: 52m 52s	remaining: 1h 55m 4s
62958:	total: 52m 52s	remaining: 1h 55m 4s
62959:	total: 52m 52s	remaining: 1h 55m 4s
62960:	learn: 2.4745937	test: 2.9276260	best: 2.9276241 (62952)	total: 52m 52s	remaining: 1h 55m 4s
62961:	total: 52m 52s	remaining: 1h 55m 4s
62962:	total: 52m 52s	remaining: 1h 55m 4s
62963:	total: 52m 52s	remaining: 1h 55m 4s
62964:	total: 52m 52s	remaining: 1h 55m 4s
62965:	learn: 2.4745535	test: 2.9276188	best: 2.9276188 (62965)	total: 52m 52s	remaining: 1h 55m 4s
62966:	total: 52m 52s	remaining: 1h 55m 4s
62967:	total: 52m 52s	remaining: 1h 55m 4s
62968:	total: 52m 52s	remaining: 1h 55m 4s
62969:	total: 52m 52s	remaining: 1h 55m 4s
62970:	learn: 2.4745229	test: 2.9276153	best: 2.9276135 (62966)	total: 52m 52s	remaining: 1h 55m 4s
62971:	total: 52m 52s	remaining: 1h 55m 4s
62972:	total: 52m 52s	remaining: 1h 55m 4s
62973:	total: 52m 52s	remaining: 1h 55m 4s
62974:	total: 52m 53s	remaining: 1h 55m 4s
62975:	learn: 2.4744892	test: 2.9276175	best: 2.9276135

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [6]:
trained_model.best_score_

{'learn': {'MAE': 2.3201570444669506, 'RMSE': 3.2591121432006167},
 'validation': {'MAE': 2.9142461956683583, 'RMSE': 4.205166179943652}}

### 6. Test

In [7]:
pred = trained_model.predict(test)

In [8]:
submission = '../../data/sample_submission.csv'

results = pd.read_csv(submission)
pred = pd.DataFrame(pred, columns=['target'])
results[['target']] = pred
results.to_csv('../../data/sample_submission_catboost.csv', index=False)